In [2]:
import os
import cv2
import matplotlib.pyplot as plt
from src.segmentation.evaluation.ultralytics_evaluator import UltralyticsEvaluator

def plot_image(image, title):
    """Function to plot an image using matplotlib."""
    plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
    plt.title(title)
    plt.axis('off')
    plt.show()


def create_trichome_dataset(annotations_directory, images_directory, output_directory, extend_percentage=0):
    # Initialize the evaluator
    ultralytics_evaluator = UltralyticsEvaluator(num_classes=3, image_size=512)

    # Get ground truth boxes
    dataset_gt_boxes = ultralytics_evaluator.get_annotations_for_dataset(annotations_directory)

    # Create output directories for each class
    classes = ['clear', 'cloudy', 'amber']
    for cls in classes:
        os.makedirs(os.path.join(output_directory, cls), exist_ok=True)

    # Process each image and crop trichomes
    for image_number, patches_gt_boxes in dataset_gt_boxes.items():
        for patch_file_name, gt_boxes in patches_gt_boxes.items():
            image_path = os.path.join(images_directory, patch_file_name)
            image = cv2.imread(image_path)

            if image is None:
                print(f"Image {image_path} not found or unable to read.")
                continue

            for i, gt in enumerate(gt_boxes):
                class_id = gt['class_id']
                bbox = gt['bbox']
                x_min, y_min, x_max, y_max = map(int, bbox)

                # Calculate the width and height of the bounding box
                width = x_max - x_min
                height = y_max - y_min

                # Calculate the extension for width and height
                width_extension = int(width * extend_percentage)
                height_extension = int(height * extend_percentage)

                # Extend the bounding box coordinates
                x_min = max(x_min - width_extension, 0)
                y_min = max(y_min - height_extension, 0)
                x_max = min(x_max + width_extension, image.shape[1])
                y_max = min(y_max + height_extension, image.shape[0])

                # Crop the trichome with extended bounding box
                trichome_crop = image[y_min:y_max, x_min:x_max]

                # Save the cropped image
                class_name = classes[class_id]
                output_path = os.path.join(output_directory, class_name, f"{image_number}_trichome_{i}.png")
                cv2.imwrite(output_path, trichome_crop)

                print(f"Cropped trichome saved at: {output_path}")

                # Plot the cropped image
                # plot_image(trichome_crop, f"{class_name} trichome from {image_number}_{i}")


### Create the test trichomes dataset

In [3]:
import os
from src.segmentation.evaluation.ultralytics_evaluator import UltralyticsEvaluator

# define paths
dataset_path = "/home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44"
images_dir_path = os.path.join(dataset_path, "v0.1")
yolo_annotations_dir_path = os.path.join(dataset_path, "annotations", "yolo", "labels", "export_coco-instance_etaylor_cannabis_patches_test_26-04-2024_15-44-44_v0.1")

ultralytics_evaluator = UltralyticsEvaluator(num_classes=3, image_size=512)
dataset_gt_boxes = ultralytics_evaluator.get_annotations_for_dataset(yolo_annotations_dir_path)
segments_path = "/home/etaylor/code_projects/thesis/segments"

In [ ]:
# create the regular trichome test dataset
output_directory = os.path.join(segments_path, os.path.basename(dataset_path), "trichome_dataset")

# Ensure the output directory exists
os.makedirs(output_directory, exist_ok=True)

# Create trichome dataset
create_trichome_dataset(yolo_annotations_dir_path, images_dir_path, output_directory)

#### Create trichome  test dataset with bigger size images

In [5]:
images_sizes = [0.1, 0.25, 0.5, 0.75, 1]

# create the datset for each size
for size in images_sizes:
    
    size_str = str(size).replace(".", "")
    # create the trichome dataset
    output_directory = os.path.join(segments_path, os.path.basename(dataset_path), f"trichome_dataset_{size_str}")

    # Ensure the output directory exists
    os.makedirs(output_directory, exist_ok=True)

    # Create trichome dataset
    create_trichome_dataset(yolo_annotations_dir_path, images_dir_path, output_directory, extend_percentage=size)

Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44/trichome_dataset_01/clear/IMG_0058_trichome_0.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44/trichome_dataset_01/cloudy/IMG_0058_trichome_1.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44/trichome_dataset_01/clear/IMG_0058_trichome_2.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44/trichome_dataset_01/clear/IMG_0058_trichome_3.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44/trichome_dataset_01/clear/IMG_0058_trichome_4.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_test_26-04-2024_15-44-44/trichome_dataset_01/clo

### Create the train trichomes dataset

In [4]:
# define paths
dataset_path = "/home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44"
images_dir_path = os.path.join(dataset_path, "v0.1")
yolo_annotations_dir_path = os.path.join(dataset_path, "annotations", "yolo", "labels", "export_coco-instance_etaylor_cannabis_patches_train_26-04-2024_15-44-44_v0.1")


In [ ]:
# create the train regular dataset
output_directory = os.path.join(segments_path, os.path.basename(dataset_path), "trichome_dataset")

# get the ground truth boxes
dataset_gt_boxes = ultralytics_evaluator.get_annotations_for_dataset(yolo_annotations_dir_path)

# Ensure the output directory exists
os.makedirs(output_directory, exist_ok=True)

# Create trichome dataset
create_trichome_dataset(yolo_annotations_dir_path, images_dir_path, output_directory)

#### Create trichome  train dataset with bigger size images

In [6]:
images_sizes = [0.1, 0.25, 0.5, 0.75, 1]

# create the test dataset for the each size
for size in images_sizes:
    
    size_str = str(size).replace(".", "")
    # create the trichome dataset
    output_directory = os.path.join(segments_path, os.path.basename(dataset_path), f"trichome_dataset_{size_str}")

    # Ensure the output directory exists
    os.makedirs(output_directory, exist_ok=True)

    # Create trichome dataset
    create_trichome_dataset(yolo_annotations_dir_path, images_dir_path, output_directory, extend_percentage=size)

Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44/trichome_dataset_01/cloudy/IMG_2163_trichome_0.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44/trichome_dataset_01/cloudy/IMG_2163_trichome_1.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44/trichome_dataset_01/amber/IMG_2163_trichome_2.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44/trichome_dataset_01/amber/IMG_2163_trichome_3.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44/trichome_dataset_01/cloudy/IMG_2163_trichome_4.png
Cropped trichome saved at: /home/etaylor/code_projects/thesis/segments/etaylor_cannabis_patches_train_26-04-2024_15-44-44/trichome_datase